In [4]:
import sqlite3

import numpy as np
# It is apparently officially accepted to explicitly
# list all the functions you need from numpy:
from numpy import array, zeros, exp, random, dot
from numpy import shape, reshape, meshgrid, linspace
from numpy import hstack, vstack

import pandas as pd
print('Panda Version:', pd.__version__)

# Set ipython's max row display
pd.set_option('display.max_row', 100, 'display.max_columns', 25)

import matplotlib.pyplot as plt # for plotting
import matplotlib
matplotlib.rcParams['figure.dpi'] = 100 # highres display

import tensorflow as tf
from tensorflow import Variable

from tensorflow.keras import Sequential
from tensorflow.keras import Model
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import TimeDistributed, RepeatVector

from keras.optimizers import SGD

from keras.models import load_model
from keras.callbacks import EarlyStopping
from keras.callbacks import ModelCheckpoint

from keras.layers import LSTM, Dense, Concatenate

from keras.optimizers import SGD

import collections
from collections import Counter

# Import date class from datetime module
import time
# import datetime as dt
from datetime import date, datetime
print("Today date is: ", date.today())

Panda Version: 2.2.2
Today date is:  2024-06-06


In [28]:
!pwd

!ls -la /workspace/data/crypto_md/

/workspace/leo
total 6528
drwxrwxr-x 1 oleg oleg     250 Jun  6 10:00 .
drwxrwxr-x 1 oleg oleg      18 Jun  3 23:40 ..
-rw------- 1 oleg oleg 1449984 Jun  4 00:49 20240601.mktdata.ohlcv.db
-rw------- 1 oleg oleg 1445888 Jun  3 23:44 20240602.mktdata.ohlcv.db
-rw------- 1 oleg oleg 1437696 Jun  4 16:45 20240603.mktdata.ohlcv.db
-rw------- 1 oleg oleg 1269760 Jun  5 10:00 20240604.mktdata.ohlcv.db
-rw------- 1 oleg oleg 1081344 Jun  6 10:00 20240605.mktdata.ohlcv.db


In [24]:
mktdata_db_file = "/workspace/data/crypto_md/20240601.mktdata.ohlcv.db"

In [ ]:
db_conn = sqlite3.connect(mktdata_db_file)

In [31]:
tables_df = pd.read_sql_query("select * from sqlite_master where type = 'table'", db_conn)
print (tables_df.head())

    type                 name             tbl_name  rootpage  \
0  table    bnbfut_ohlcv_1min    bnbfut_ohlcv_1min         2   
1  table   bnbspot_ohlcv_1min   bnbspot_ohlcv_1min        66   
2  table  coinbase_ohlcv_1min  coinbase_ohlcv_1min       224   

                                                 sql  
0  CREATE TABLE bnbfut_ohlcv_1min (tstamp INTEGER...  
1  CREATE TABLE bnbspot_ohlcv_1min (tstamp INTEGE...  
2  CREATE TABLE coinbase_ohlcv_1min (tstamp INTEG...  


In [34]:
df = pd.read_sql_query("select * from coinbase_ohlcv_1min", db_conn)
df.tail()

tstamp exchange_id instrument_id    open    high     low  \
5754  1717286100000000000    COINBASE  PAIR-XRP-USD  0.5183  0.5183  0.5180   
5755  1717286160000000000    COINBASE  PAIR-XRP-USD  0.5180  0.5182  0.5180   
5756  1717286220000000000    COINBASE  PAIR-XRP-USD  0.5181  0.5181  0.5180   
5757  1717286280000000000    COINBASE  PAIR-XRP-USD  0.5181  0.5183  0.5181   
5758  1717286340000000000    COINBASE  PAIR-XRP-USD  0.5182  0.5184  0.5181   

       close        volume      vwap  
5754  0.5180   7401.243996  0.518096  
5755  0.5180   3491.632415  0.518020  
5756  0.5181   6963.191620  0.518095  
5757  0.5182  35743.462893  0.518140  
5758  0.5184  45521.897366  0.518245

In [ ]:
# 0601 - 0605

In [33]:
df["timestamp"] = pd.to_datetime(df['tstamp'], unit='ns')
df.set_index("timestamp", inplace=True)
print (df.head())

                                  tstamp exchange_id instrument_id      open  \
timestamp                                                                      
2024-06-01 00:00:00  1717200000000000000    COINBASE  PAIR-BTC-USD  67473.07   
2024-06-01 00:01:00  1717200060000000000    COINBASE  PAIR-BTC-USD  67506.57   
2024-06-01 00:02:00  1717200120000000000    COINBASE  PAIR-BTC-USD  67494.73   
2024-06-01 00:03:00  1717200180000000000    COINBASE  PAIR-BTC-USD  67512.78   
2024-06-01 00:04:00  1717200240000000000    COINBASE  PAIR-BTC-USD  67538.81   

                         high       low     close    volume          vwap  
timestamp                                                                  
2024-06-01 00:00:00  67514.99  67468.13  67506.03  2.045049  67496.869352  
2024-06-01 00:01:00  67515.00  67480.66  67494.74  0.646759  67500.893305  
2024-06-01 00:02:00  67515.00  67455.91  67514.99  9.732906  67477.840770  
2024-06-01 00:03:00  67553.85  67496.58  67539.76  4.374730

In [ ]:
df_union = pd.read_sql_query("select * from coinbase_ohlcv_1min", db_conn)